In [ ]:
!pip install segment-geospatial leafmap localtileserver pycrs -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 13.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.4/19.4 MB 57.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.2/40.2 kB 4.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.6/14.6 MB 66.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 61.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.0/20.0 MB 52.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 72.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.0/5.0 MB 67.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 56.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 96.5/96.5 kB 8.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 130.5/130.5 kB 13.5 MB/s eta 0:00:00


In [ ]:
# Bibliotecas
import os
import leafmap
from samgeo import SamGeo, tms_to_geotiff, get_basemaps

In [ ]:
m = leafmap.Map()
m.add_basemap("SATELLITE")
m

Map(center=[-17, -48], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_t…

In [ ]:
# Definindo bbox
if m.user_roi_bounds() is not None:
    bbox = m.user_roi_bounds()
else:
    bbox = [-43.0606178935068087,-22.9085543339510593, -43.0585899991957461,-22.9075835528617446]

In [ ]:
# Arquivo de imagem
image = "/content/ortofoto_RJ.tif"

In [ ]:
# Tif para tile 
tms_to_geotiff(output=image, bbox=bbox, zoom=20, source="Satellite", overwrite=True)

Downloaded image 01/28
Downloaded image 02/28
Downloaded image 03/28
Downloaded image 04/28
Downloaded image 05/28
Downloaded image 06/28
Downloaded image 07/28
Downloaded image 08/28
Downloaded image 09/28
Downloaded image 10/28
Downloaded image 11/28
Downloaded image 12/28
Downloaded image 13/28
Downloaded image 14/28
Downloaded image 15/28
Downloaded image 16/28
Downloaded image 17/28
Downloaded image 18/28
Downloaded image 19/28
Downloaded image 20/28
Downloaded image 21/28
Downloaded image 22/28
Downloaded image 23/28
Downloaded image 24/28
Downloaded image 25/28
Downloaded image 26/28
Downloaded image 27/28
Downloaded image 28/28
Saving GeoTIFF. Please wait...
Image saved to /content/ortofoto_RJ.tif


In [ ]:
m.layers[-1].visible = False  # turn off the basemap
m.add_raster(image, layer_name="CTU")
m

Map(bottom=4739.0, center=[-17, -48], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_titl…

In [ ]:
checkpoint = os.path.join("model", "sam_vit_h_4b8939.pth")

In [ ]:
# Instanciando modelo
sam = SamGeo(
    model_type="vit_h",
    checkpoint=checkpoint,
    sam_kwargs=None,
)

Checkpoint model/sam_vit_h_4b8939.pth does not exist.


Downloading...
From: https://dl.fbaipublicfiles.com/segment_anything/sam_vit_h_4b8939.pth
To: /content/model/sam_vit_h_4b8939.pth
100%|██████████| 2.56G/2.56G [00:15<00:00, 160MB/s]


In [ ]:
# Gerando máscaras
mask = "mask.tif"
sam.generate(
    image, mask , batch=True, foreground=True, erosion_kernel=(3, 3), mask_multiplier=255
)

100%|██████████| 8/8 [35:54<00:00, 269.29s/it]


In [ ]:
# Gravando em .shp
shapefile = "NIT.shp"
sam.tiff_to_vector(mask, shapefile)

In [ ]:
# Visualizando
style = {
    "color": "#3388ff",
    "weight": 2,
    "fillColor": "#7c4185",
    "fillOpacity": 0.5,
}
m.add_vector(shapefile, layer_name="NIT")
m

Map(bottom=75886941.0, center=[-22.908048047130826, -43.059633672237396], controls=(ZoomControl(options=['posi…